# BIM relationship detection


Notebook for performing relationship detection using design files.

#### Input:
1. Design file structure extracted from navisworks NWD file.
2. IFC file generated from NWD file
3. graph predictions from GNN

#### Sections:
1. Relationship identification: Identify, extract and (visualize) 
aggregation and connectivity relationships.
2. Visalization: Deprecated
3. IFC to cloud: Create point clouds from each element in IFC file
4. Graph dataset: Create a graph dataset from relationship information
 
 (GNN training available in link_prediction.ipynb notebook)
5. Evaluate GNN: Evaluate predictions from GNN
6. Visalize predictions: Draw IFC element to visualize FP,TP,FNs
7. Analyze dataset and results: Repetition removal, element category analysis


In [1]:
# setup

%load_ext autoreload
%autoreload 2

In [43]:
# general
import json
import collections
import math
import uuid
import random
import pickle
import os
from itertools import islice
from pathlib import Path
import numpy as np

# ifc and pointcloud
import ifcopenshell
import open3d as o3d
#import pymeshlab as ml
from compas.geometry import oriented_bounding_box_numpy
from scipy.spatial import distance
from ifcopenshell.util.selector import Selector

# graph 
import dgl
from dgl.data import DGLDataset
import torch

from src.structure import get_systems, get_branches
from src.ifc import draw_relationship, setup_ifc_file
from src.geometry import element_distance
from src.cloud import element_to_cloud
from src.graph import process_nodes, process_edges, IndustrialFacilityDataset, get_node_features
from src.icp import run_command
from src.geometry import sq_dist_vect, vector_mag
from src.centerline import get_centerline_deviation, get_centerline_distance
# vis
# from ipywidgets import interact
# from OCC.Core.Bnd import Bnd_Box, Bnd_OBB
# from OCC.Core.BRepBndLib import brepbndlib_AddOBB
# from OCC.Core.BRepPrimAPI import (BRepPrimAPI_MakeBox, 
# BRepPrimAPI_MakeSphere, BRepPrimAPI_MakeCylinder)
# from OCC.Core.gp import gp_Pnt, gp_XYZ, gp_Ax2, gp_Dir

# from utils.JupyterIFCRenderer import JupyterIFCRenderer
from tqdm.notebook import tqdm_notebook as tqdm

In [3]:
# load design file structure
data_path = "/mnt/c/data/3D_CAD/"
system_dict_file = data_path + "WestDeckBox.nwd_aggregation.json"
#system = 'West-DeckBox-Piping.rvm'
system = 'West-DeckBox-Pipe.rvm'

blueprint = 'data/sample.ifc'
temp_dir = "output/east2/"
ifcConvert_executable = "scripts/./IfcConvert"


#m = ifcopenshell.open("data/231110AC-11-Smiley-West-04-07-2007.ifc")k

## Relationship Identification

###  aggrgegation relationships

In [ ]:
get_systems(system_dict_file)    

### Topological relationships

In [ ]:
branches = get_branches(system_dict_file)[system]

In [ ]:
# requisties for IFC file creation

create_guid = lambda: ifcopenshell.guid.compress(uuid.uuid1().hex)
m = ifcopenshell.open("../merged.ifc")
owner_history = m.by_type("IfcOwnerHistory")[0]
project = m.by_type("IfcProject")[0]
context = m.by_type("IfcGeometricRepresentationContext")[0]
floor = m.by_type("IfcBuildingStorey")[0]


In [ ]:
# draw links between connected elements, return connections
def visualize_branches(branches, ifc, floor=None, owner_history=None, context=None, draw=False, contiguous=True, dist_thresh=0.002):
    pipe_type = 'IFCPIPESEGMENT'
    fitting_type = 'IFCPIPEFITTING'

    pipe_selector = Selector()
    fitting_selector = Selector()
    pipes = pipe_selector.parse(ifc, '.' + pipe_type)
    fittings = fitting_selector.parse(ifc, '.' + fitting_type)
    fitting_names = [f.Name for f in fittings]
    pipe_names = [p.Name for p in pipes]
    print(pipes[0].Name)

    vis_dict = {}
    for k, val in branches.items():
        vis_elements = []
        connect = True
        for element in val:
            if element in pipe_names:
                vis_elements.append((element, pipe_type, connect))
                connect = True
            elif element in fitting_names:
                vis_elements.append((element, fitting_type, connect))
                connect = True
            else:
                connect = False
        vis_dict[k] = vis_elements

    error_count = 0
    count = 0
    rels = []
    selector = Selector()
    
    # enumerate through branches
    for k, val in tqdm(vis_dict.items()):
#         if count == 10:
#             break
        branch_size = len(val)
        for i, element in enumerate(val):
            #check if element is not the last element
            if (i+1) < branch_size:
                try:
                    
                    if val[i+1][2] or not contiguous:
                        rels.append([(element[0], element[1]), 
                                  (val[i+1][0], val[i+1][1])])
                        if draw:
                            element1 = selector.parse(
                                m, '.' + element[1] + '[Name *= "' + element[0] + '"]')[0]
                            element2 = selector.parse(
                                m, '.' + val[i+1][1] + '[Name *= "' + val[i+1][0] + '"]')[0]
                            draw_relationship(element[0], element1, 
                                  val[i+1][0], element2, ifc, floor, owner_history, context)
                
                    else:
                        element1 = selector.parse(
                            m, '.' + element[1] + '[Name *= "' + element[0] + '"]')[0]
                        element2 = selector.parse(
                            m, '.' + val[i+1][1] + '[Name *= "' + val[i+1][0] + '"]')[0]
                        
                        if element_distance(element1, element2, ifc) < dist_thresh:
                            rels.append([(element[0], element[1]), 
                                  (val[i+1][0], val[i+1][1])])
                            if draw:
                                draw_relationship(element[0], element1, 
                                  val[i+1][0], element2, ifc, floor, owner_history, context)
                except Exception as e:
                    #print (e)
                    error_count +=1
        count +=1

    print(error_count)
    return rels


In [ ]:
rels = visualize_branches(branches, m, floor, owner_history, context, True)
# rels = visualize_branches(branches, m)

In [ ]:
print(len(rels), rels[0])

In [ ]:
import pickle
with open('../top_rels_eastdeckbox_test.pkl', 'wb') as f:
    pickle.dump(rels, f)

In [ ]:
m.write('../east_vis_test.ifc')

## Visualization

In [ ]:
# viewer = JupyterIFCRenderer(m, size=(400,300))
# viewer.setAllTransparent()
# viewer

### aggregation relationships

In [ ]:
# picker = viewer.colorPicker()
# picker


In [ ]:
# out_dict = {'HVAC':['Rohrtypen:Kupfer - Hartgelötet:7718868', 'Rohrtypen:Kupfer - Hartgelötet:7718886', ],
#            'electrical':[ 'Rohrtypen:Kupfer - Hartgelötet:7718872', 'Rohrtypen:Kupfer - Hartgelötet:7718880']}

# # PAINT A SET OF ELEMENTS IN ONE COLOUR
# def systemSelect(system):
#     selector = Selector()
#     for e in out_dict[system]:
#         element = selector.parse(m, '.IfcProduct[Name *= "' + e + '"]')[0]
#         viewer.setColor(element, picker.value)
#     return system

# interact(systemSelect, system=['HVAC', 'electrical'])

Instances of building elements with represenations can be selected interactivly. Information such as the attributes `GUID`, `Name` etc. are displayed to the left of the 3D viewport.

In [ ]:
# # reset colours
# viewer.setDefaultColors()

### topological relationships



#### replace jupyter renderer

1. Compute the bounding box of ifc product directly from points
2. generate ifc elements to indicate relationships


In [ ]:
# test

# element_name = "TUBE 1 of BRANCH /AM-8120227-WD-MDA-01/B1"
# element_type = "IFCPIPESEGMENT"

# selector = Selector()
# element = selector.parse(
#     m, '.' + element_type + '[Name *= "' + element_name + '"]')[0]

# shape = element.Representation.Representations[0].Items[0]
# element_coords = np.array(shape.Coordinates.CoordList)
# #print(element_coords)
# bbox = oriented_bounding_box_numpy(element_coords)
# print(bbox)

In [ ]:
# test

# element1_name = "TUBE 1 of BRANCH /AM-8120227-WD-MDA-01/B1"
# element1_type = "IFCPIPESEGMENT"
# element2_name = "ELBOW 1 of BRANCH /AM-8120227-WD-MDA-01/B1"
# element2_type = "IFCPIPEFITTING"

# element3_name = "TUBE 2 of BRANCH /AM-8120227-WD-MDA-01/B1"
# element3_type = "IFCPIPESEGMENT"
# element4_name = "ELBOW 2 of BRANCH /AM-8120227-WD-MDA-01/B1"
# element4_type = "IFCPIPEFITTING"
# element5_name = "TUBE 3 of BRANCH /AM-8120227-WD-MDA-01/B1"
# element5_type = "IFCPIPESEGMENT"

# draw_relationship(element1_name, element1_type, 
#                   element2_name, element2_type, m)
# draw_relationship(element2_name, element2_type, 
#                   element3_name, element3_type, m)
# draw_relationship(element3_name, element3_type, 
#                   element4_name, element4_type, m)
# draw_relationship(element4_name, element4_type, 
#                   element5_name, element5_type, m)
#element1_center, element1_coords = get_element_deets()



# centerpoint =gp_Pnt(element1_center)
# ball = BRepPrimAPI_MakeSphere(centerpoint, 0.02).Shape()

In [ ]:
# element.Representation.Representations[0].Items[0].CoordIndex = element.Representation.Representations[0].Items[0].CoordIndex[:1]

## IFC to cloud

sample points from ifc model

In [ ]:
# parse through individual ifc files for each model type and sample point clouds
#ifc = ifcopenshell.open(data_path +"deckboxelbow_ref.ifc")
ifc = ifcopenshell.open(temp_dir +"TEE.ifc")


In [ ]:
element_type = 'IFCPIPEFITTING'
#element_type = 'IFCPIPESEGMENT'
selector = Selector()
tees = selector.parse(ifc, '.' + element_type)
print(len(tees))

In [ ]:
# normalise an element and convert it into an obj
def element_to_obj(element, save_path, blueprint, temp_dir, ifcConvert_executable):
    # setup new ifc
    ifc = setup_ifc_file(blueprint)
    owner_history = ifc.by_type("IfcOwnerHistory")[0]
    project = ifc.by_type("IfcProject")[0]
    context = ifc.by_type("IfcGeometricRepresentationContext")[0]
    floor = ifc.by_type("IfcBuildingStorey")[0]

    ifc_info = {"owner_history": owner_history,
        "project": project,
       "context": context, 
       "floor": floor}
    
    # normalise points
    points = np.array([e for e in ifc.traverse(element) if e.is_a("IfcCartesianPointList3D")][0][0])
    mean = np.mean(points, axis=0)
    norm_points = points - mean
    norm_factor = np.max(np.linalg.norm(norm_points, axis=1))*3/1000
    norm_points /= norm_factor
    #print(norm_factor, mean, element.id())
    [e for e in ifc.traverse(element) if e.is_a("IfcCartesianPointList3D")][0][0] = norm_points.tolist()

    # add element to new ifc
    ifc.add(element)
    tmp_ifc = os.path.join(temp_dir, 'tmp.ifc')
    ifc.write(tmp_ifc)
    
    # convert ifc to obj
    cmds = (ifcConvert_executable, tmp_ifc, save_path)
    result = run_command(cmds)
    
    return mean.tolist(), norm_factor
    

In [ ]:
# convert an element to an obj
metadata_path = data_path + "bp_east_metadata.json"
category = {}
with open(metadata_path, "r") as jsonFile:
    metadata = json.load(jsonFile)

for i, element in enumerate(tqdm(tees)):
    save_path = data_path +"east_tee_obj/" + str(i) + ".obj"
    mean, norm_factor = element_to_obj(element, save_path, blueprint, temp_dir, ifcConvert_executable)
    category[str(i)] = {"mean":mean, "norm_factor":norm_factor, "id":element.id()}
    
metadata["tee"] = category
with open(metadata_path, "w") as jsonFile:
    json.dump(metadata, jsonFile)

In [ ]:
# convert an element to a point cloud directly
metadata_path = data_path + "bp_east_metadata.json"
category = {}
with open(metadata_path, "r") as jsonFile:
    metadata = json.load(jsonFile)

for i, element in enumerate(tqdm(tees)):
    save_path = data_path +"east_tee_cloud/" + str(i) + ".pcd"
    cloud = element_to_cloud(element, save_path, 2048)
    category[str(i)] = {"id":element.id()}
    
#print(category)
metadata["tee"] = category
with open(metadata_path, "w") as jsonFile:
    json.dump(metadata, jsonFile)

## Graph dataset

### get nodes & edges

In [ ]:
types = ['FLANGE', 'ELBOW', 'TEE', 'TUBE', 'BEND']
node_info = process_nodes(ifc, types)

In [ ]:
print(len(node_info), len(node_info[0]), len(node_info[1]))

with open('../nodes_eastdeckbox_test.pkl', 'wb') as f:
    pickle.dump(node_info, f)

In [ ]:
with open('../top_rels_eastdeckbox.pkl', 'rb') as f:
    rels = pickle.load(f)
with open('../nodes_eastdeckbox.pkl', 'rb') as f:
    node_info = pickle.load(f)
    nodes = node_info[0]
    
edges = process_edges(ifc, nodes, rels)

In [ ]:
with open('../edges_eastdeckbox_test.pkl', 'wb') as f:
    pickle.dump(edges, f)

In [ ]:
# sanity checks

# print(points.shape, labels.shape, centers.shape, lengths.shape, directions.shape)
# print(points[0][0], labels[0], centers[0], lengths[0], directions[0])
# print(5 in labels)

# edges_src = edges[:,0]
# edges_dst = edges[:,1]
# print(edges_src)
# print(np.max(edges_dst))

### create dataset

In [ ]:
dataset = IndustrialFacilityDataset()
graph = dataset[0]

print(graph)

## Evaluate GNN

In [4]:
# load edges
model_path = 'gnn_params/'

with open(model_path + '/eval/pos_edges_test.pkl', 'rb') as f:
            u, v = pickle.load(f)
with open(model_path + '/eval/neg_edges_test.pkl', 'rb') as f:
            neg_u_full,neg_v_full = pickle.load(f)
print(len(neg_u_full), len(u))


283235946 29784


In [5]:
# load predicted scores
with open(model_path + '/eval/pos_score_test.pkl', 'rb') as f:
            pos_score = pickle.load(f)
with open(model_path + '/eval/neg_score_test.pkl', 'rb') as f:
            neg_score= pickle.load(f)


In [6]:
print(len(neg_score), len(pos_score))

283235946 29784


Calculate confusion matrix coefficiants

In [7]:
threshold = 0.5
FNs, TPs, FPs, TNs = [], [], [], []

# TPs / FNs
for i, score in enumerate(pos_score):
    sig = 1/(1 + np.exp(-score))
    if sig > threshold:
        TPs.append([u[i].item(), v[i].item()])
    else:
        FNs.append([u[i].item(), v[i].item()])

# FPs
for i, score in enumerate(tqdm(neg_score)):
    sig = 1/(1 + np.exp(-score))
    if sig > threshold:
        FPs.append([neg_u_full[i], neg_v_full[i]])

print(len(TPs), len(FPs), len(FNs) )
TPs = np.array(TPs)
FPs = np.array(FPs)
FNs = np.array(FNs)

  0%|          | 0/283235946 [00:00<?, ?it/s]

29649 38422292 135


In [8]:
print(1/(1 + np.exp(-neg_score[0])))

0.9539102090414475


In [9]:
with open(model_path + '/eval/metrics_test.pkl', 'wb') as f:
    pickle.dump([TPs, FPs, FNs], f)

In [10]:
with open(model_path + '/eval/metrics_test.pkl', 'rb') as f:
    TPs, FPs, FNs = pickle.load(f)

Calculate raw metrics

In [11]:
precision = len(TPs)/(len(TPs)+len(FPs))
recall = len(TPs)/(len(TPs)+len(FNs))
accuracy = (len(TPs)-len(FPs) +len(neg_score))/(len(neg_score)+len(pos_score))
print(precision, recall, accuracy)

0.0007710664072848755 0.9954673650282031 0.8643590701917948


Refinement based on element distances (eliminate predictions beyond a distance threshold)

In [5]:
def get_edges_from_node_info(node):
    c = np.array(node[1])
    l = max(node[2])/2
    d = np.array(node[3])

    return ((c+l*d), (c-l*d))


In [8]:
def check_predictions_fast(preds, point_info, node_info, dist_thresh=0.002, rough_dist_thresh=0.1):
    refined_preds = []
    
    for pair in tqdm(preds):
        #rough distance check using two edges
        bb0 = get_edges_from_node_info(node_info[pair[0]])
        bb1 = get_edges_from_node_info(node_info[pair[1]])
        if ((sq_dist_vect(bb0[0], bb1[0]) < rough_dist_thresh) or
            (sq_dist_vect(bb0[0], bb1[1]) < rough_dist_thresh) or
            (sq_dist_vect(bb0[1], bb1[0]) < rough_dist_thresh) or
            (sq_dist_vect(bb0[1], bb1[1]) < rough_dist_thresh)):
            
            # slower, precise check using points
            dist = np.min(distance.cdist(
                point_info[pair[0]], point_info[pair[1]], 'sqeuclidean'))
            if (dist < dist_thresh):
                refined_preds.append(pair)
    return refined_preds

In [7]:
site = 'eastdeckbox'
#data_path = '../'
node_file = "nodes_" + site + ".pkl"
with open(data_path + node_file, 'rb') as f:
    node_info = pickle.load(f)

In [9]:
# check if positive predictions fall within distance threshold
def check_predictions(preds, point_info, dist_thresh=0.002):
    refined_preds = []
    
    for pair in tqdm(preds):
        #print(len(point_info), pair[0], pair[1])        
        dist = np.min(distance.cdist(
            point_info[pair[0]], point_info[pair[1]], 'sqeuclidean'))
        if (dist < dist_thresh):
            refined_preds.append(pair)
    return refined_preds

In [32]:
print(refined_TPs[0])

[    0 14022]


In [15]:
# refined_TPs = check_predictions(TPs, node_info[1])
# refined_FPs = check_predictions(FPs, node_info[1])

refined_TPs = check_predictions_fast(TPs, node_info[1], node_info[0])
refined_FPs = check_predictions_fast(FPs, node_info[1], node_info[0])
print(len(refined_TPs), len(refined_FPs))

  0%|          | 0/29649 [00:00<?, ?it/s]

  0%|          | 0/38422292 [00:00<?, ?it/s]

29591 32248


In [41]:
def get_centerline_deviation(ad, bd):
    centerline_deviation = np.arccos( np.dot(ad, bd))
    #print(math.degrees(centerline_deviation), ad, bd)
    if centerline_deviation > np.pi/2:
        centerline_deviation = np.pi - centerline_deviation
    return centerline_deviation


def get_distance_to_intersection(a, b):
    centerline_connecting_line = np.cross(a[3], b[3])
    center_connecting_line = b[1] - a[1]
    centerline_distance = (abs(np.dot(centerline_connecting_line, 
                                          center_connecting_line)) / 
                           vector_mag(centerline_connecting_line))
    sq_mag_ccl = np.dot(centerline_connecting_line, 
                        centerline_connecting_line)
    t1 = np.dot(np.cross(b[3], centerline_connecting_line),
                center_connecting_line) / sq_mag_ccl
    t2 = np.dot(np.cross(a[3], centerline_connecting_line),
                center_connecting_line) / sq_mag_ccl
    
    return t1, t2

In [64]:
def get_rdp(feat, e):
    r = feat[1+e]
    p = [feat[4+e*3], feat[5+e*3], feat[6+e*3]]
    d = [feat[13+e*3], feat[14+e*3], feat[15+e*3]]
    return r, d, p


# TODO: scale thresholds with radius
def connectivity_refinements(preds, node_info, params_path, dataset, radius_threshold, 
                             centerline_angle_threshold, centerline_dist_threshold):
    # load predicted node params
    features = get_node_features(node_info, params_path, dataset, [])
    features = features.cpu().detach().numpy()
    #rint(features.shape, max(np.array(preds)[:,0]), max(np.array(preds)[:,1]))
    refined_preds = []
    r_count, dev_count, dist_count = 0, 0, 0
    
    for pair in tqdm(preds):
        accepted = False
        feat1 = features[pair[0]]
        feat2 = features[pair[1]]
        
        # iterate through edges of first element
        for e1 in range(3):
            if accepted:
                break
            r1, d1, p1 = get_rdp(feat1, e1)
            if r1 == 0.:
                continue
            
            # iterate through edges of first element
            for e2 in range(3):
                if accepted:
                    break
                r2, d2, p2= get_rdp(feat2, e2)
                if r2 == 0.:
                    continue

                # radius check
                #print(r1, r2, r1/r2 ,r2/r1 )
                if (r1/r2 > radius_threshold) and (r2/r1 > radius_threshold):
                    r_count += 1

                    # centerline direction check
                    centerline_deviation = get_centerline_deviation(d1, d2)
                    #print(centerline_deviation, centerline_angle_threshold)
                    if centerline_deviation < centerline_angle_threshold:
                        dev_count +=1

                        #print ("dists", math.sqrt(sq_dist_vect(p1, p2)), (r1+r2))
                        if math.sqrt(sq_dist_vect(p1, p2)) < (r1+r2):
                            
                        # centerline proximity check
#                         tn1 = [0, np.array(p1), 0, np.array(d1)] # temp node feature
#                         tn2 = [0, np.array(p2), 0, np.array(d2)] # temp node feature
#                         centerline_distance = get_centerline_distance(tn1, tn2)
#                         if centerline_distance < centerline_dist_threshold:
                            
                            # centerline co-planar check
                            #print("dist", get_distance_to_intersection(tn1, tn2))
                            dist_count += 1
                            refined_preds.append(pair)
                            accepted = True
    
    print(r_count, dev_count, dist_count)
    return refined_preds

In [65]:
radius_threshold = 0.1
centerline_angle_threshold = math.radians(90) # angle threshold for two pipes to be considered parallel
centerline_dist_threshold = 0.01 # centerline distance threshold pipes to be to considered connected
params_path = Path('output/east_ref/')
dataset = "east"

refined_refined_TPs = connectivity_refinements(refined_TPs, node_info, params_path, dataset, radius_threshold,
                                              centerline_angle_threshold, centerline_dist_threshold)

refined_refined_FPs = connectivity_refinements(refined_FPs, node_info, params_path, dataset, radius_threshold,
                                              centerline_angle_threshold, centerline_dist_threshold)


1855
3979
508
8211
2278


  0%|          | 0/3979 [00:00<?, ?it/s]

cl elbow 3979


  0%|          | 0/508 [00:00<?, ?it/s]

cl tee 4487


...

cl flange 8620


  0%|          | 0/8211 [00:00<?, ?it/s]

cl pipe 16831
16831
10 16831


  0%|          | 0/32248 [00:00<?, ?it/s]

123604 123604 1323


In [66]:
print(len(refined_refined_TPs)/len(refined_TPs), len(refined_refined_FPs)/len(refined_FPs))

0.7254908587070393 0.04102580004961548


In [16]:
with open(model_path + '/eval/refined_test.pkl', 'wb') as f:
    pickle.dump([refined_TPs, refined_FPs], f)

In [10]:
with open(model_path + '/eval/refined_test.pkl', 'rb') as f:
    refined_TPs, refined_FPs = pickle.load(f)
print(len(refined_TPs))

29591


Refined metrics

In [17]:
precision = len(refined_TPs)/(len(refined_TPs)+len(refined_FPs))
recall = len(refined_TPs)/(len(refined_TPs)+len(FNs))
accuracy = (len(refined_TPs)-len(refined_FPs) +len(neg_score))/(len(neg_score)+len(pos_score))
print(precision, recall, accuracy)

0.478516793609211 0.9954585211599274 0.9998854750272826


ROC curve

In [18]:
pos_score= pos_score[:int(len(pos_score)/10)]
neg_score= pos_score[:int(len(neg_score)/10)]

In [19]:
len(neg_score)

2978

In [20]:
scores = np.concatenate([pos_score, neg_score])

In [21]:
sig = 1/(1 + np.exp(-scores))

In [22]:
from sklearn.metrics import RocCurveDisplay
import matplotlib.pyplot as plt


RocCurveDisplay.from_predictions(labels, scores)
plt.show()

NameError: name 'labels' is not defined

## visualize predictions

In [23]:
ifc = ifcopenshell.open(data_path+"/east_merged.ifc")

In [24]:
create_guid = lambda: ifcopenshell.guid.compress(uuid.uuid1().hex)
owner_history = ifc.by_type("IfcOwnerHistory")[0]
project = ifc.by_type("IfcProject")[0]
context = ifc.by_type("IfcGeometricRepresentationContext")[0]
floor = ifc.by_type("IfcBuildingStorey")[0]


In [25]:
red = ifc.createIfcColourRgb('red', Red=0.9, Green=0.0, Blue=0.0)
green = ifc.createIfcColourRgb('green', Red=0.0, Green=0.9, Blue=0.0)
yellow = ifc.createIfcColourRgb('yellow', Red=0.9, Green=0.9, Blue=0.0)

In [26]:
# visualize results on ifc file
def draw_predictions(preds, nodes, ifc, colour):
    for pair in tqdm(preds):
        element1 = ifc.by_id(nodes[pair[0]][4])
        element1_name = element1.Name
        element2 = ifc.by_id(nodes[pair[1]][4])
        element2_name = element2.Name
        
        draw_relationship(element1_name, element1, element2_name, 
                          element2, ifc, floor, owner_history, context, colour)

In [27]:
print(len(refined_TPs), len(refined_FPs), len(FNs))

29591 32248 135


In [28]:
draw_predictions(refined_TPs, node_info[0], ifc, green)

  0%|          | 0/29591 [00:00<?, ?it/s]

[34.42974853515625, 3.4388959407806396, 50.6659280342404] [34.42864648301176, 3.4326295315504303, 50.809720311060005] 0.21141353106185418
[10.910950660705591, 3.5650000572204568, 49.0670002352998] [10.927539791753828, 3.5564937350949117, 49.19635664666215] 0.00821524980758236
[10.910950660705591, 3.5650000572204568, 48.19600025298139] [10.894287758164351, 3.573361966936322, 48.06664383978922] 0.00821524980758236
[12.668700218200692, -0.24517315626144187, 48.27946090698245] [12.654924966591395, -0.22131414155622428, 48.1795490254152] 0.03919500244481934
[10.1317179921831, -7.87062311172485, 54.74283599853515] [10.22947788232705, -7.87062311172485, 54.74283599853515] 0.02160546107672591
[18.95999908447265, 15.9211948718336, 49.72999954223635] [18.93245048691515, 15.77254466841935, 49.7299995422363] 0.03919500242917806
[18.95999908447265, 16.9287997875902, 49.72999954223635] [18.987549589378823, 17.077449037330176, 49.7299995422363] 0.03919500242917806
[35.16999816894534, 20.9492223591153

[19.07706260681155, 18.3921563782338, 46.9119987487793] [19.077062606811552, 18.2436828613281, 46.9119987487793] 0.05750675222941604
[19.07706260681155, 18.575136407410703, 46.9119987487793] [19.077062606811552, 18.739370332449276, 46.94473610038242] 0.05778500474987336
[22.54999923707787, -14.397572517980151, 46.80393981960779] [22.550072936526888, -14.448934951937611, 46.82914897154069] 0.039006266155079385
[1.4830180020987078, 16.47311849449833, 50.84472285817513] [1.4912699460983134, 16.6011807409165, 50.84467315673827] 0.01274226751772993
[1.4830180020987078, 16.47311849449833, 50.84472285817513] [1.3982994283749532, 16.376729818732926, 50.844673156738295] 0.01274226751772993
[23.994306563145493, 14.159999847305206, 52.17724990958688] [23.913378573643598, 14.160036942704316, 52.24648226884375] 0.012805624097492715
[23.994306563145493, 14.159999847305206, 52.17724990958688] [24.075228403555958, 14.159950145975284, 52.10800270121706] 0.012742267517709583
[11.449626578810442, 6.14057

[1.491269946098325, 19.0907332334291, 50.7015609741211] [1.4912699460983299, 19.237214606633632, 50.73107953704314] 0.012350000813604989
[1.491269946098325, 16.6011803713072, 50.7015609741211] [1.4830180020987074, 16.47311849449833, 50.70161067555793] 0.012742267517725284
[16.590000152587898, -16.393799776903197, 52.70615005493165] [16.61755065749405, -16.542449189918052, 52.7061500549316] 0.03919500242917806
[16.590000152587898, -15.8361997653332, 52.70615005493165] [16.562235314633895, -15.687764685366103, 52.70676431986587] 0.04087192480310923
[27.250785629268943, 21.666149953103478, 50.48030090329857] [27.137277570858018, 21.67164935192249, 50.4803009033203] 0.03044031262401923
[28.124775170904574, 21.666148325546523, 50.48030090329857] [28.248500825374997, 21.660732916324903, 50.48571426537674] 0.030441188798236343
[10.734552983515998, 9.788610458374025, 47.6484794616699] [10.86195276581255, 9.77791021667924, 47.6484794616699] 0.021710001863548458
[10.724000330693, 9.7886104583740

[34.207164764404304, -13.935774124314, 50.86777877807614] [34.23471336196185, -13.787124441368551, 50.8677787780762] 0.03919500242917806
[34.207164764404304, -15.013700211693399, 50.86777877807614] [34.23471336196185, -15.16234989334825, 50.8677787780762] 0.03919500242917806
[16.268572700416755, 18.55032373619349, 55.16769076269589] [16.198554751856985, 18.61846591096117, 55.26876512129143] 0.012350000771510354
[16.268572700416755, 18.55032373619349, 55.16769076269589] [16.278751373290987, 18.46088790893555, 55.15299987792967] 0.012350000771510354
[29.966839812259423, -14.432839415530925, 52.1500015258789] [29.92799949645995, -14.583299636840799, 52.1500015258789] 0.016430500257952865
[29.966839812259423, -14.432839415530925, 52.1500015258789] [30.041999816894503, -14.39400005340575, 52.1500015258789] 0.01643050025798309
[15.280820767739687, 12.501042013321712, 50.11899948122564] [15.173506302421, 12.499899864196788, 50.11899948120117] 0.008215250129377029
[15.280820767739687, 12.50104

...

[37.68672885021351, -16.2427978515625, 47.951692548885404] [37.731708526611335, -16.242797851562518, 47.89892959594724] 0.03044031262401923
[37.68672885021351, -16.2427978515625, 47.951692548885404] [37.681228637577256, -16.24279743107379, 48.065199996861494] 0.03044031262401923
[4.298615656290697, -16.0737484707854, 53.954628711532735] [4.134436628874391, -16.040956497192347, 53.95531845092775] 0.05974610041278271
[4.315944312570337, -16.091077127065024, 53.954628711532735] [4.34873676300049, -16.255256308889003, 53.95531845092775] 0.05974610041278271
[36.72502136256133, -6.6739694919210475, 46.23892828472242] [36.72502136224221, -6.805685305953835, 46.23593423672458] 0.041275184898431745
[36.72502136256133, -6.6739694919210475, 46.23892828472242] [36.72502136204807, -6.607316509161301, 46.240445641746334] 0.041275184898431745
[26.576189259246586, -10.431304423924495, 52.35964069486397] [26.675114342707268, -10.34440832422386, 52.35979843139652] 0.039361450815440714
[26.57618925924658

[11.183649394210452, 11.471967584949502, 52.49593980849475] [11.183500289917001, 11.340589151229, 52.5045013427734] 0.0372391676355947
[35.11274604628805, -4.182400226593015, 47.84395103286025] [35.2146759033203, -4.1824002265930185, 47.81639862060544] 0.039195002429186145
[35.11274604628805, -4.182400226593015, 47.84395103286025] [35.0851936340332, -4.19915008942189, 47.9561004638672] 0.039195002429186145
[37.3257542429301, -4.405754643473275, 48.1734504699707] [37.3199996948242, -4.52372487546561, 48.1734504699707] 0.03044031262401923
[37.3257542429301, -4.405754643473275, 48.1734504699707] [37.443724815873395, -4.40000009536743, 48.1734504699707] 0.03044031262401923
[10.022868665188398, -13.581952133722215, 55.59099777295755] [10.027852058410625, -13.579074859619126, 55.6689682006836] 0.030440437505013573
[10.022868665188398, -13.581952133722215, 55.59099777295755] [9.920703514763817, -13.640937926438225, 55.58524322528428] 0.030440437505013573
[32.53914970727675, -10.3300495147705,

[18.29051569116627, -18.73694589567124, 52.67860145723259] [18.30999755859375, -18.756425857543952, 52.5299528963081] 0.03919500318724118
[18.29051569116627, -18.73694589567124, 52.67860145723259] [18.225402832112763, -18.67183113106297, 52.70615005493166] 0.03919500318724118
[14.4135503768921, -5.67360019683838, 48.53855042971555] [14.4135503768921, -5.67360019683838, 48.406798567715995] 0.04127482300103154
[11.873220082565158, 17.766290304612326, 50.32553494576794] [11.8676996231079, 17.7663555145264, 50.2056013261219] 0.021869524022285508
[11.873220082565158, 17.766290304612326, 50.32553494576794] [11.93341159950844, 17.76635551452633, 50.39353180061926] 0.021869524022285508
[28.60604279404776, 12.111812399312697, 51.91937003309012] [28.75465529140307, 12.084262847900401, 51.915995503161064] 0.03919500417148421
[28.60604279404776, 12.111812399312697, 51.91937003309012] [28.578500747680643, 12.2604628372103, 51.91999435424805] 0.03919500417148421
[5.602549837334143, -13.4564764039683

[16.683000564575202, -3.7560533687309077, 55.0250541373924] [16.6830005645752, -3.7699995040893555, 54.900899632972404] 0.017355000786499455
[14.680830942729393, 0.2803119234282243, 53.04675389613776] [14.6185197832071, 0.2800063192844293, 53.03286743164061] 0.02033963289876632
[14.680830942729393, 0.2803119234282243, 53.04675389613776] [14.694720268249512, 0.2800063192844294, 53.1090660097086] 0.02033963289876632
[7.6016881834822385, -8.387304559150037, 46.03866718886741] [7.601718307866268, -8.255588340114143, 46.04165771396211] 0.04127518451459484
[7.6016881834822385, -8.387304559150037, 46.03866718886741] [7.6016728509093685, -8.45395730454608, 46.0371499192928] 0.04127518452618935
[16.2728353192506, -12.727999687194835, 46.882999420166044] [16.176574472527403, -12.727999687194842, 46.882999420165994] 0.03124382439187996
[34.858744428856355, -4.182400226593015, 46.925551222069245] [35.00739490089649, -4.182400226593019, 46.89799880981445] 0.039195002429186145
[34.858744428856355, -

[29.20499992370605, 23.320800858530653, 52.616849822011346] [29.20499992370605, 23.315046310424798, 52.5238800048828] 0.03044031262395457
[32.065296967343905, -12.34717257769551, 48.576999664306655] [32.05134963989261, -12.471326998518, 48.57699966430661] 0.017355000786432484
[32.065296967343905, -12.34717257769551, 48.576999664306655] [32.189449759758894, -12.33322715759281, 48.57699966430661] 0.017355000786432484
[37.96880449644824, 14.892885800872559, 46.90307006987672] [37.92636365456448, 14.912237061118484, 46.97287391426598] 0.04953048897801082
[37.96880449644824, 14.892885800872559, 46.90307006987672] [38.03276901679776, 14.90130947399322, 46.832365917306824] 0.07456588614356059
[4.085742017970682, 22.013202086975905, 52.7834091135317] [4.085289955232037, 21.853798708019106, 52.78207891421957] 0.11330759346965592
[3.9673214982880816, 22.180630892785363, 52.90562912529054] [3.8555075004171853, 22.178676605224624, 53.01923190807582] 0.11330759346965592
[9.59690013712222, -7.870623

In [29]:
draw_predictions(refined_FPs, node_info[0], ifc, yellow)

  0%|          | 0/32248 [00:00<?, ?it/s]

[10.910950660705591, 3.5650000572204568, 49.0670002352998] [10.91094970703125, 3.53099894523621, 48.238678539266594] 0.00821524980758236
[10.910950660705591, 3.5650000572204568, 49.0670002352998] [10.927409987617015, 3.5222449562035747, 49.196356646612216] 0.00821524980758236
[10.910950660705591, 3.5650000572204568, 49.0670002352998] [10.910950660705591, 3.5939998626708967, 49.0670002352998] 0.008215249807582488
[10.910950660705591, 3.5650000572204568, 49.0670002352998] [10.927539791753828, 3.5854937789639316, 49.19635664666215] 0.00821524980758236
[10.910950660705591, 3.5650000572204568, 48.19600025298139] [10.86848354342873, 3.59018169235255, 48.17552466469874] 0.008215250100532843
[10.910950660705591, 3.5650000572204568, 48.19600025298139] [10.897767805989407, 3.607182716114059, 48.06664383969968] 0.00821524980758236
[10.910950660705591, 3.5650000572204568, 48.19600025298139] [10.873383522482607, 3.532415389843299, 48.08246612546618] 0.008215250689772921
[10.910950660705591, 3.56500

[15.622000694274899, 12.6564998626709, 50.2379987503439] [15.5930004119873, 12.6245002746582, 50.2602500931436] 0.008215250128949055
[15.622000694274899, 12.6564998626709, 50.2933733309656] [15.6220006942749, 12.6245002746582, 50.2970011393507] 0.008215250128949055
[15.622000694274899, 12.6564998626709, 50.2379987503439] [15.6102661808864, 12.610013021201786, 50.16764176436469] 0.00821525012894851
[15.622000694274899, 12.6564998626709, 50.2933733309656] [15.593000411987301, 12.6564998626709, 50.28144455089075] 0.00821525012894851
[15.622000694274899, 12.6564998626709, 50.2379987503439] [15.58125351978343, 12.64201294086925, 50.19665228082417] 0.008725864470422152
[15.622000694274899, 12.6564998626709, 50.2933733309656] [15.563784599029649, 12.624500274763003, 50.416965487302214] 0.00821525024703925
[15.622000694274899, 12.6564998626709, 50.2933733309656] [15.590631369150913, 12.62451033299622, 50.36573104938562] 0.00821525012894851
[15.622000694274899, 12.6564998626709, 50.293373330965

[23.994306563145493, 14.159999847305206, 52.17724990958688] [23.97740688035409, 14.155504303801264, 52.28509925028585] 0.0254845350354741
[15.59624576657945, 12.5319004058838, 50.0260009765625] [15.74335753370545, 12.53190040588375, 50.073643809068045] 0.008215249488145178
[15.59624576657945, 12.5319004058838, 50.0260009765625] [15.455999376527682, 12.515899658627927, 50.055000304749754] 0.008215250927144525
[15.59624576657945, 12.5319004058838, 50.0260009765625] [15.613491587645399, 12.531900405883821, 50.05500030517578] 0.008215250128950342
[15.59624576657945, 12.5319004058838, 50.0260009765625] [15.506177028350079, 12.530758255546129, 50.05500020998868] 0.008215249488145178
[15.59624576657945, 12.5319004058838, 50.0260009765625] [15.455999376527688, 12.515899658627912, 50.02600097613646] 0.008215250927125531
[-0.339696915436575, 17.415660858154318, 52.422176361083984] [-0.24017421998966948, 17.410439376194383, 52.451152261021406] 0.008215250128950623
[-0.339696915436575, 17.41566085

[0.32612721916479703, 17.307420048204687, 52.4515865292374] [0.3308258217560981, 17.29982851902703, 52.41556167602535] 0.012477639788542237
[0.32612721916479703, 17.307420048204687, 52.4515865292374] [0.26886248575121185, 17.237449645137577, 52.41556167606596] 0.012477639788542237
[11.865079935557393, 17.282468874332764, 52.2955627441322] [11.777159900279493, 17.31145095826331, 52.33756270652467] 0.012322874595107577
[11.865079935557393, 17.282468874332764, 52.2955627441322] [11.9567498544366, 17.313199996948253, 52.25956344604495] 0.012322874570012726
[11.865079935557393, 17.282468874332764, 52.2955627441322] [11.889551647940701, 17.31352837801044, 52.3375601965209] 0.012198792493476381
[23.587179183959982, -14.433157920837404, 48.8877931067547] [23.587177276462658, -14.42340946195085, 48.747608184853085] 0.012322874282642877
[22.665000914092893, 13.8190002441406, 52.2837486281434] [22.75841398094854, 13.819049945577529, 52.26300148051392] 0.012742267517736898
[22.665000914092893, 13.

...

[10.764499680171351, 3.401522636413575, 47.76940058075395] [10.805685997009299, 3.20646989215699, 47.7038993835449] 0.02171000186354355
[10.764499680171351, 3.401522636413575, 47.76940058075395] [10.82999987702535, 3.401522614753008, 47.91820318131734] 0.02171000186354355
[26.799999237060547, 14.1255498328012, 49.5] [26.799999237060547, 14.192049940605749, 49.5] 0.04127544259403431
[7.6016728509093685, -8.45395730454608, 46.0371499192928] [7.661680697948666, -8.580649376369951, 46.033706665303946] 0.04127518452618935
[20.8990566584055, 22.487704171025353, 53.236326575556525] [20.9784267095144, 22.487704171025353, 53.236326575556525] 0.04953077901213145
[9.134167671203615, -7.870623111724855, 54.22465534882015] [9.134167671203615, -7.870623111724855, 54.29473876892005] 0.03663400169462139
[17.987700089605873, 16.763875993595075, 55.419460296630845] [17.8931999206543, 16.770433348622703, 55.4252148447367] 0.03044031262401923
[40.66908825453447, -11.247548991641464, 45.833130014302924] [4

[19.6785997605766, 17.612867355346644, 47.78200149536131] [19.523155212402372, 17.612867355346673, 47.699575827165944] 0.04540280039073892
[9.78349590441554, -12.853414365321825, 55.75810844567458] [9.71605990792031, -12.947999954223658, 55.75269317626953] 0.03044075047097591
[9.78349590441554, -12.853414365321825, 55.75810844567458] [9.783495903015133, -12.9001350377221, 55.804828641237705] 0.03044075047097591
[36.40728378295895, 15.0905647277832, 47.4601646326324] [36.407283782959, 15.0905647277832, 47.593726454696004] 0.03137097142945997
[35.74305464612712, 18.9091567993164, 52.008569927217174] [35.84543359763328, 18.909156931079576, 52.168152863535255] 0.07429500333969906
[12.66129478627865, 0.3755493145627295, 49.46701049804685] [12.668700218200701, 0.252816542094288, 49.4670104980469] 0.03663156572731659
[13.432396146245297, 9.921095084923387, 55.64904001122419] [13.537506992447707, 9.948644638061516, 55.5439282111045] 0.039195000396287594
[34.056652070118716, 4.27604495561497, 5

[29.84194171289544, -10.808211697353961, 52.48905579251916] [29.68473233404677, -10.914153878725326, 52.492150363965784] 0.07429598277344392
[22.54999923531735, -14.326315481588095, 46.76280093440132] [22.54999923707787, -14.397572517980151, 46.80393981960779] 0.039006266155079385
[22.54999923531735, -14.326315481588095, 46.76280093440132] [22.713499780995903, -14.311809539794947, 46.75442504882816] 0.039006265567473455
[35.57862962334185, 6.232850074768072, 48.098197937011726] [35.65407562449837, 6.2328495981152665, 48.09819793707642] 0.013778332866233535
[35.57862962334185, 6.232850074768072, 48.098197937011726] [35.59780012519335, 6.232850074768053, 48.09819793701173] 0.010401408787574696
[3.6643650970450703, -15.956740943958875, 57.17773350911388] [3.668835623742964, -16.065211368459796, 57.264439396436416] 0.07456588614355802
[36.65287017822265, -7.53818988800049, 49.5579486288828] [36.65287017822265, -7.53818988800049, 49.624451120873104] 0.04127482270574134
[4.583041206274396, -

[36.12204340028987, 10.109024396497926, 49.8452895089359] [36.09834670827005, 9.931305883831854, 49.8500595090246] 0.0741022717736887
[0.6888037774169775, -6.075102329510028, 46.24701836716845] [0.5512059307910936, -6.1459269540967085, 46.25081253053527] 0.04127499123335335
[37.753349304199205, -14.91254978011375, 49.2371494310069] [37.753349304199205, -14.8850002288818, 49.141749862828846] 0.03919500242918268
[12.110076904296871, 0.780368342355359, 47.271999359130824] [12.138833403282195, 0.6730474324713689, 47.271999359130874] 0.045402589529219155
[10.48466682439905, -5.9712300300598145, 54.166999816894545] [10.37936687432065, -5.971230030059807, 54.16699981689452] 0.021605461076707445
[20.68000030517574, 19.094999313354467, 54.29917643371405] [20.6800003051758, 19.0949993133545, 54.3872029542851] 0.06191099390196513
[2.799425862494763, 12.295653849033812, 53.00064218311223] [2.611645237712289, 12.336531274365079, 53.00475016491997] 0.03936145229997318
[46.9700012207031, 17.209999084

[26.789370642817367, 21.13373050429955, 47.362748741826245] [26.799999237060547, 21.2766653183143, 47.4143414069324] 0.10335000604389481
[27.8000011444092, -14.7449998855591, 49.141749862828846] [27.80000114440915, -14.74499988555905, 49.288501573907794] 0.039006265567488665
[9.85406017303467, -13.698699527132199, 55.7420411637899] [9.796312129087589, -13.709437002038836, 55.671256668092866] 0.02184630304938689
[37.38570022583009, 19.549999237060547, 46.834919413109404] [37.38570022583011, 19.549999237060547, 46.768249074439396] 0.04127482270573673
[30.49578857421875, -2.5350804724496703, 45.93900299072265] [30.495788573919953, -2.403355853874415, 45.941276798361926] 0.04127513264990717
[30.49578857421875, -2.5350804724496703, 45.93900299072265] [30.49578857421875, -2.6017504534918, 45.93900299072265] 0.04127513264990717
[37.40000152587891, 19.549552917480455, 53.161905025691496] [37.40000152587891, 19.549552917480455, 53.23492457941105] 0.04540404051631697
[37.494998931884794, 15.0500

In [30]:
draw_predictions(FNs, node_info[0], ifc, red)

  0%|          | 0/135 [00:00<?, ?it/s]

[4.453000068664555, 17.79393100901452, 52.722298162529384] [4.45300006868018, 18.0096295284182, 52.72229647757661] 0.02160546112063387
[10.27770423728855, 13.187685966491712, 50.05585479736325] [10.386720849769125, 13.215236471397876, 50.055854797363295] 0.03919500242918268
[15.8404998779297, 18.1172501366844, 50.65499877929685] [15.8404998779297, 18.322749816890898, 50.6549987792969] 0.008215250128947428
[28.2549991607666, 8.307330838198618, 50.14099884033205] [28.2549991607666, 8.47082996368408, 50.15139987469435] 0.0390062655674935
[13.352399920354841, 20.92399978637695, 52.519451144754505] [13.189477245095242, 20.92399978637695, 52.54079649201955] 0.07429500333963439
[19.038585662841804, 18.98943710327145, 47.95209884626095] [19.0385856628418, 18.956699751668317, 47.846364988595674] 0.057785004749940326
[9.579999923706048, 13.1249078832176, 49.866153717041] [9.588505298975871, 13.25630305166601, 49.866311453573545] 0.039361450815436835
[18.762275343673497, 14.412000656127901, 52.64

[15.0801000595093, 21.546781568411998, 50.9550018310547] [15.085594425186857, 21.66672464800594, 50.9550892008896] 0.02184994599990783
[14.98009967803955, 21.5881824885272, 50.9550018310547] [14.985594043717168, 21.70812365008111, 50.955089200889596] 0.021849945999907704
[12.944000244155086, 10.739609761714387, 52.00355948476107] [12.944440493927928, 10.906218146199578, 51.98436188253966] 0.10982290112648652
[18.14999961853025, 15.93135356903075, 52.94564819335935] [18.177550123436475, 15.827553556663974, 52.9456481933594] 0.03919500242918268
[14.680100440979, 21.712381776812602, 50.9550018310547] [14.685593852982276, 21.83232447100398, 50.9550892008896] 0.021849945999892782
[8.081332206726074, 13.1773729324341, 48.0539168363352] [8.0870868284064, 13.17737293243405, 48.17665180379575] 0.036631565727314276
[1.1880250250006301, 21.7462100982666, 52.1435508728027] [1.40372506148706, 21.7462100982666, 52.1435508728027] 0.02160546107671206
[15.8725004196167, 18.3472503001161, 50.65499877929

In [31]:
ifc.write(model_path + '/eval/pred_vis_test_ref.ifc')

## Additional refinements

### remove repetitions

In [ ]:
# as the graph is bidirected, a single edge has two predictions. 
# This function removes repetitions in a single set of predictions.
def remove_repetitions(preds):
    non_rep = []
    for i, pair in enumerate(tqdm(preds)):
        found = False
        for j, pair2 in enumerate(preds[i:]):
            if pair[0] == pair2[1] and pair[1] == pair2[0]:
                found = True
                #break
        if not found:
            non_rep.append(pair)
    
    return non_rep

In [ ]:
# same as above, except for removing repetitions across two sets of predictions
# ex. between true positives and false negatives
def compare_preds(preds1, preds2):
    for i in range(len(preds1)):
        preds1[i].sort()
    for i in range(len(preds2)):
        preds2[i].sort()
    non_rep = []
    
    for i, pair in enumerate(preds1):
        found = False
        for j, pair2 in enumerate(preds2):
            if pair[0] == pair2[0] and pair[1] == pair2[1]:
                found = True
                break
        if not found:
            non_rep.append(pair)
    
    return non_rep

In [ ]:
print(len(refined_TPs))
non_rep_TPs = remove_repetitions(refined_TPs)
print(len(non_rep_TPs))

In [ ]:
print(len(refined_FPs))
non_rep_FPs = remove_repetitions(refined_FPs)
print(len(non_rep_FPs))

In [ ]:
print(len(FNs))
non_rep_FNs = remove_repetitions(FNs)
print(len(non_rep_FNs))

In [ ]:
refined_FNs = compare_preds(non_rep_FNs, non_rep_TPs)
print(len(non_rep_FNs), len(refined_FNs))

Refined metrics after removing repetitions

In [ ]:
precision = len(non_rep_TPs)/(len(non_rep_TPs)+len(non_rep_FPs))
recall = len(non_rep_TPs)/(len(non_rep_TPs)+len(non_rep_FNs))
accuracy = (len(non_rep_TPs)-len(refined_FPs) +len(neg_score))/(len(neg_score)+len(pos_score))
print(precision, recall, accuracy)

In [ ]:
with open(model_path + '/eval/east_non_rep_test.pkl', 'wb') as f:
    pickle.dump([non_rep_TPs, non_rep_FPs, non_rep_FNs], f)

Calculate metrics for each element category

### Analyse dataset and results

In [ ]:
# element type wise precision recall analysis
def sort_type(preds, nodes):
    bins = np.zeros([4,4])
    for p in preds:
        x=nodes[p[0]][0]
        y= nodes[p[1]][0]
        if x == 4:
          x = 3
        if y == 4:
          y = 3
        li = [x,y]
        li.sort()
        x,y = li[0],li[1]
        
        bins[x][y] += 1
    return bins

In [ ]:
tp_bins = sort_type(non_rep_TPs,node_info[0] )
fp_bins = sort_type(non_rep_FPs,node_info[0] )
fn_bins = sort_type(non_rep_FNs,node_info[0] )

In [ ]:
print(tp_bins)

In [ ]:
recall = tp_bins/(tp_bins+fn_bins)
precision = tp_bins/(tp_bins+fp_bins)

In [ ]:
print(precision)
print(recall)

In [ ]:
print("F1:", (2*precision*recall)/(precision+recall))

Calculate element types in dataset

In [ ]:
# analyse dataset

# load data
site = 'east'

def analyse_dataset(site):
  data_path = "/content/drive/MyDrive/graph/"
  edge_file = "edges_" + site + "deckbox.pkl"
  node_file = "nodes_" + site + "deckbox.pkl"
  with open(data_path + node_file, 'rb') as f:
      node_info = pickle.load(f)
  with open(data_path + edge_file, 'rb') as f:
      edges = pickle.load(f)

  # get element type counts
  labels = np.array([i[0] for i in node_info[0]])
  unique, counts = np.unique(labels, return_counts=True)
  print(dict(zip(unique, counts)))

  # get connection counts
  counts = np.zeros((5,5), dtype=int)

  for edge in edges:
    x = labels[edge[0]]
    y = labels[edge[1]]
    if x == 4:
      x = 3
    if y == 4:
      y = 3
    li = [x,y]
    li.sort()
    x,y = li[0],li[1]
    counts[x][y] += 1

  return(counts)

c_east = analyse_dataset('east')
c_west = analyse_dataset('west')
count = c_east + c_west
print(count)

### Dataset creation v2

The dataset must have shared element ids across both the pointclouds used for parameter inference and the graph node dataset. The steps for creating the new dataset are;
1. create subsets of merged.ifc for the 4 classes (include bend in elbow) preserving element id
2. run refinement to get refined_ifcs (manual deletion)
3. generate pointcloud dataset from ifcs
4. get the element ids of refined ifcs, compare with ids in the graph and delete extra nodes / edges to get refined graph

1. create subsets of merged.ifc for the 4 classes (include bend in elbow) preserving element id

In [ ]:
def get_elements_from_ifc(ifc):
    ifc_full = ifcopenshell.open(ifc)
    selector = Selector()
    element_type = 'IFCPIPEFITTING'
    elements_fitting = selector.parse(ifc_full, '.' + element_type)
    element_type = 'IFCPIPESEGMENT'
    elements_segments = selector.parse(ifc_full, '.' + element_type)
    elements = elements_segments + elements_fitting
    print(len(elements))
    return elements

In [ ]:
# load ifc
elements = get_elements_from_ifc(data_path +"east_merged.ifc")

In [ ]:
# load nodes
with open(data_path + 'nodes_eastdeckbox.pkl', 'rb') as f:
    node_info = pickle.load(f)
    nodes = node_info[0]
    
print(len(nodes))

# load edges
with open(data_path + 'edges_eastdeckbox.pkl', 'rb') as f:
    edges = pickle.load(f)
    
print(edges[0])

In [ ]:
# get matching elements between nodes and elements
matching_elements = {}

for i, el in enumerate(tqdm(elements)):
    for j, node in enumerate(nodes):
        if el.id() == node[4]:
            matching_elements[str(j)] = i
            

In [ ]:
b = [b for b in nodes if b[0]]
print(len(matching_elements), nodes[0])

In [ ]:
# filter by class
#types = ['FLANGE', 'ELBOW', 'TEE', 'TUBE', 'BEND']
types = ['BEND']
combined_metadata = {}
for k, tp in enumerate(types):
    class_metadata = {}
    
    # setup new ifc
    ifc = setup_ifc_file(blueprint)
    owner_history = ifc.by_type("IfcOwnerHistory")[0]
    project = ifc.by_type("IfcProject")[0]
    context = ifc.by_type("IfcGeometricRepresentationContext")[0]
    floor = ifc.by_type("IfcBuildingStorey")[0]
    k = 4
    # add element to new ifc
    for i, nd in enumerate(tqdm(nodes)):
        # check if class matches
        #print(matching_elements[str(i)])
        count = 0
        if nd[0] == k:
            el = elements[matching_elements[str(i)]]
            new_id = ifc.add(el).id()
            class_metadata[str(new_id)] = el.id()
            #print(el.id(), new_id)
            
    combined_metadata[tp] = class_metadata
    
    # write ifc
    tmp_ifc = os.path.join(temp_dir, tp+'.ifc')
    ifc.write(tmp_ifc)
    


In [ ]:
print(len(combined_metadata["BEND"].keys()))

In [ ]:
f = open(os.path.join(temp_dir, 'id_metadata.json'), 'w')
json.dump(combined_metadata, f)

step 2 and 3 must be carried out using IFCPARSE script (or manually) and using element_to_cloud function (or using blender for tees)

4. get the element ids of refined ifcs, compare with ids in the graph and delete extra nodes / edges to get refined graph

In [ ]:
# identify nodes which have been deleted
total_ids = []
for k, tp in enumerate(types):
    elements = get_elements_from_ifc(os.path.join(temp_dir, tp+'_ref.ifc'))
    element_ids = [combined_metadata[tp][str(el.id())] for el in elements]
    total_ids += element_ids

print(len(total_ids))
missing_count = 0

for nd in nodes:
    if nd[4] not in total_ids:
        missing_count += 1
print("missing", missing_count)


In [ ]:
print(len(set(total_ids)))

In [ ]:
# create modified graph with refined nodes
new_nodes, new_node_points, new_edges = [], [], []
id_dict = {}
for i in range(len(nodes)):
    id_dict[str(i)] = None
    
for i, nd in enumerate(nodes):
    if nd[4] in total_ids:
        new_nodes.append(nd)
        new_node_points.append(node_info[1][i])
        id_dict[str(i)] = len(new_nodes)-1
        
print(len(new_nodes), new_nodes[0])

for e in edges:
    if id_dict[str(e[0])] is not None and id_dict[str(e[1])] is not None:
        new_edges.append((id_dict[str(e[0])], id_dict[str(e[1])]))
        
print(len(new_edges), new_edges[0])

In [ ]:
with open(os.path.join(temp_dir, 'nodes_westdeckbox_ref.pkl'), 'wb') as f:
    pickle.dump([new_nodes, new_node_points], f)
    
with open(os.path.join(temp_dir, 'edges_westdeckbox_ref.pkl'), 'wb') as f:
    pickle.dump(new_edges, f)
